In [6]:
import pandas as pd
import numpy as np
from PIL import Image
import os
import matplotlib.pyplot as plt

K means algorithm

In [1]:
def initialise_centroids(k,data):
    centroids_idx = np.random.choice(len(data), k, replace=False)
    centroids = [data[i] for i in centroids_idx]
    return centroids

In [2]:
def assign_to_clusters(data, centroids):
    """
    Assign each data point to the nearest centroid.
    """
    clusters = [[] for _ in range(len(centroids))]
    for point in data:
        distances = [np.linalg.norm(np.array(point) - np.array(c)) for c in centroids]
        cluster_idx = np.argmin(distances)
        clusters[cluster_idx].append(point)
    return clusters


In [3]:
def update_centroids(clusters):

    centroids = [np.mean(cluster, axis=0) for cluster in clusters]
    return centroids


In [22]:
# Function to compute likelihood
def compute_likelihood(pixel, clusters, wk=0.1):
    likelihood = 0
    for cluster in clusters:
        distance = np.linalg.norm(np.array(pixel) - np.array(cluster))
        likelihood += np.exp(-distance) * wk
    return likelihood


In [12]:
# Function to perform K-Means Clustering
def kmeans(data, k, max_iterations=100):
    centroids = initialise_centroids(k, data)
    for _ in range(max_iterations):
        clusters = assign_to_clusters(data, centroids)
        new_centroids = update_centroids(clusters)
        # Check for convergence
        if np.array_equal(new_centroids, centroids):
            break
        centroids = new_centroids
    return clusters, centroids


Preprocessing

In [11]:
# preprocessing for lady stroke 1

# Open the image
lady_stroke1 = Image.open("Q1 Dataset/lady stroke 1.png")

# Get pixel data
pixel_data = list(lady_stroke1.getdata())

# # Convert flat pixel data into RGB tuples
# lady_stroke1_data = [(r, g, b) for r, g, b in pixel_data]

In [13]:
lady_cluster, lady_centroids = kmeans(pixel_data, 64)

c:\Users\siddi\AppData\Local\Programs\Python\Python311\Lib\site-packages\numpy\core\fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
c:\Users\siddi\AppData\Local\Programs\Python\Python311\Lib\site-packages\numpy\core\_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


KeyboardInterrupt: 

In [15]:
import numpy as np
from PIL import Image
import os

# K-Means Algorithm
def initialize_centroids(k, data):
    centroids_idx = np.random.choice(len(data), k, replace=False)
    centroids = [data[i] for i in centroids_idx]
    return centroids

def assign_to_clusters(data, centroids):
    clusters = [[] for _ in range(len(centroids))]
    for point in data:
        distances = [np.linalg.norm(np.array(point) - np.array(c)) for c in centroids]
        cluster_idx = np.argmin(distances)
        clusters[cluster_idx].append(point)
    return clusters

def update_centroids(clusters):
    centroids = [np.mean(cluster, axis=0) for cluster in clusters if cluster]
    return centroids

def kmeans(data, k, max_iterations=100):
    centroids = initialize_centroids(k, data)
    for _ in range(max_iterations):
        clusters = assign_to_clusters(data, centroids)
        new_centroids = update_centroids(clusters)
        if np.array_equal(new_centroids, centroids):
            break
        centroids = new_centroids
    return clusters, centroids

# Preprocessing and Seed Extraction
def extract_seed_pixels(image_path):
    # Open the image
    image = Image.open(image_path)
    
    # Convert image to grayscale
    grayscale_image = image.convert('L')
    
    # Threshold to extract red and blue seed pixels
    foreground_mask = np.array(grayscale_image) == 255  # Assuming red brush-strokes are marked as white
    background_mask = np.array(grayscale_image) == 0    # Assuming blue brush-strokes are marked as black
    
    # Extract coordinates of seed pixels
    foreground_seeds = np.argwhere(foreground_mask)
    background_seeds = np.argwhere(background_mask)
    
    # Clip coordinates to ensure they are within the image bounds
    height, width = image.size
    foreground_seeds = np.clip(foreground_seeds, 0, [height-1, width-1])
    background_seeds = np.clip(background_seeds, 0, [height-1, width-1])
    
    return foreground_seeds, background_seeds


# Main Segmentation Function
def lazy_snapping_segmentation(image_path, k=64, max_iterations=100):
    # Extract seed pixels
    foreground_seeds, background_seeds = extract_seed_pixels(image_path)
    
    # Open the image
    image = Image.open(image_path)
    
    # Get pixel data
    pixel_data = list(image.getdata())
    
    # Perform K-Means clustering
    centroids = initialize_centroids(k, pixel_data)
    for iteration in range(max_iterations):
        clusters = assign_to_clusters(pixel_data, centroids)
        new_centroids = update_centroids(clusters)
        if np.array_equal(new_centroids, centroids):
            print(f"Converged after {iteration+1} iterations.")
            break
        centroids = new_centroids
        print(f"Iteration {iteration+1} completed.")
    
    # Assign pixels to seed classes
    for seed in foreground_seeds:
        seed_rgb = image.getpixel(tuple(seed))
        seed_label = np.argmin([np.linalg.norm(np.array(seed_rgb) - np.array(c)) for c in centroids])
        clusters[seed_label].append(seed)
    for seed in background_seeds:
        seed_rgb = image.getpixel(tuple(seed))
        seed_label = np.argmin([np.linalg.norm(np.array(seed_rgb) - np.array(c)) for c in centroids])
        clusters[seed_label].append(seed)
        
    return clusters, centroids

# Example usage:
image_path = "Q1 Dataset/lady stroke 1.png"
foreground_seeds, background_seeds = extract_seed_pixels(image_path)
clusters, centroids = lazy_snapping_segmentation(image_path)


Iteration 1 completed.
Converged after 2 iterations.
Iteration 1 completed.
Converged after 2 iterations.


In [17]:
print(clusters)

[[(0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0), (0, 0, 0

In [19]:
print(centroids)

[array([2.29272446, 0.        , 3.35361842])]


In [21]:
import csv
csv_file_path = "centroids.csv"

with open(csv_file_path, 'w', newline='') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerows(centroids)